In [1]:
# Importar librerías para tratamiento de datos
# -----------------------------------------------------------------------
import pandas as pd  # Pandas es una poderosa librería para manipulación y análisis de datos en Python.

# Importar librerías para web scraping y manipulación de datos
# -----------------------------------------------------------------------
from bs4 import BeautifulSoup
import requests

# Importar librerías para automatización de navegadores web con Selenium
# -----------------------------------------------------------------------
from selenium import webdriver  # Selenium es una herramienta para automatizar la interacción con navegadores web.
from webdriver_manager.chrome import ChromeDriverManager  # ChromeDriverManager gestiona la instalación del controlador de Chrome.
from selenium.webdriver.common.keys import Keys  # Keys es útil para simular eventos de teclado en Selenium.
from selenium.webdriver.support.ui import Select  # Select se utiliza para interactuar con elementos <select> en páginas web.

# Importar librerías para pausar la ejecución
# -----------------------------------------------------------------------
from time import sleep  # Sleep se utiliza para pausar la ejecución del programa por un número de segundos.

# Configuraciones
# -----------------------------------------------------------------------
pd.set_option('display.max_columns', None)  # Establece una opción de Pandas para mostrar todas las columnas de un DataFrame.

import numpy as np

import re

In [23]:
#funcion para optener el reparto de la peli desde google

def obtener_actores(lista):
    resultado_actores = []
    
    diccionario = {}
    
    driver = webdriver.Chrome() 

    url = "https://www.google.com/" 

    driver.get(url)  

    driver.maximize_window()

    sleep(1)

    driver.find_element("css selector", "#L2AGLb > div").click() # Aceptar cookies

    sleep(1)


    for indice, pelicula in enumerate(lista):

        driver.find_element("css selector", "#APjFqb").send_keys(f"reparto `{pelicula}`", Keys.ENTER)  #busco el reparto de la película en google

        sleep(4)
        print("----------")
        print(indice)
        print(pelicula)
        

        try:
            for num in range(1, 9): #cojo el nombre de cada actor que me da
                nombre_actor = driver.find_element("css selector", f"#rcnt > div.M8OgIe > div > div > div > div > div > div.uciohe > div:nth-child({num})").text.split("\n")[0]
                print(f"Actor {num}: {nombre_actor}")
                resultado_actores.append({"pelicula" : pelicula, "actor" : nombre_actor})
        except:
            pass

        sleep(4)

        driver.back()


        if indice % 50 == 0 : #cada 50 películas cierro el navegador y vuelvo a empezar para que no rompa
            
            print("reinicio navegador") 

            driver.quit()

            driver = webdriver.Chrome() 

            url = "https://www.google.com/" 

            driver.get(url)  

            driver.maximize_window()

            sleep(1)

            driver.find_element("css selector", "#L2AGLb > div").click() # Aceptar cookies

            sleep(1)
        

    driver.quit()  # Cerrar el navegador al finalizar
    return resultado_actores

In [42]:
# Llamamos a la función para sacar los actores de cada pelicula

resultados = obtener_actores(lista_peliculas1)
print(resultados)

----------
0
Pál Adrienn
reinicio navegador
----------
1
Oda az igazság
----------
2
A zöld sárkány gyermekei
----------
3
The Final Journey
----------
4
In My Sleep
Actor 1: Philip Winchester
Actor 2: Lacey Chabert
Actor 3: Abigail Spencer
Actor 4: Kelly Overton
Actor 5: Tony Hale
Actor 6: Michael Badalucco
Actor 7: Amy Aquino
Actor 8: Tim Draxl
----------
5
This Wretched Life
----------
6
Blind Sided
----------
7
Anderson's Cross
Actor 1: Jerome Elston Scott
Actor 2: Nicholas Downs
Actor 3: Heather Bergdahl
Actor 4: Michael Warren
Actor 5: Joyce Guy
Actor 6: Joanna Cassidy
Actor 7: Bill Moseley
Actor 8: Micah Stuart
----------
8
Den milde smerte
----------
9
Capture the Flag
----------
10
Utomlennye solntsem 2
Actor 1: Nikita Mijalkov
Actor 2: Nadezhda Mijalkova
Actor 3: Oleg Ménshikov
Actor 4: Yevgeny Mironov
Actor 5: Vladimir Adolfovich Ilyin
Actor 6: Serguéi Makovetski
Actor 7: Dmitri Dyuzhev
Actor 8: Andrey Merzlikin
----------
11
Tekken
Actor 1: Kelly Overton
Actor 2: Candîce Hi

In [43]:
len(resultados)

1528

In [44]:
resultados

[{'pelicula': 'In My Sleep', 'actor': 'Philip Winchester'},
 {'pelicula': 'In My Sleep', 'actor': 'Lacey Chabert'},
 {'pelicula': 'In My Sleep', 'actor': 'Abigail Spencer'},
 {'pelicula': 'In My Sleep', 'actor': 'Kelly Overton'},
 {'pelicula': 'In My Sleep', 'actor': 'Tony Hale'},
 {'pelicula': 'In My Sleep', 'actor': 'Michael Badalucco'},
 {'pelicula': 'In My Sleep', 'actor': 'Amy Aquino'},
 {'pelicula': 'In My Sleep', 'actor': 'Tim Draxl'},
 {'pelicula': "Anderson's Cross", 'actor': 'Jerome Elston Scott'},
 {'pelicula': "Anderson's Cross", 'actor': 'Nicholas Downs'},
 {'pelicula': "Anderson's Cross", 'actor': 'Heather Bergdahl'},
 {'pelicula': "Anderson's Cross", 'actor': 'Michael Warren'},
 {'pelicula': "Anderson's Cross", 'actor': 'Joyce Guy'},
 {'pelicula': "Anderson's Cross", 'actor': 'Joanna Cassidy'},
 {'pelicula': "Anderson's Cross", 'actor': 'Bill Moseley'},
 {'pelicula': "Anderson's Cross", 'actor': 'Micah Stuart'},
 {'pelicula': 'Utomlennye solntsem 2', 'actor': 'Nikita Mij

In [13]:
#funcion para buscar cada actor en wikipedia para sacar sus datos biográficos
def obtener_datos_actores(lista):
    actores_datos = []
    for indice, actor1 in enumerate(lista):
        print(indice)
        try:
            actor = actor1.replace(" ", "_") #cambiamos los espacios por barrabajas para crear las url
    
            url_actor = f"https://es.wikipedia.org/wiki/{actor}"
    
            respuesta= requests.get(url_actor)
    
            # vemos si todo ha ido bien
            print("La respuesta de la petición es:", respuesta.status_code)
            
            if respuesta.status_code == 200: 
                
                # nombre
                nombre = actor.replace("_", " ") #volvemos a poner el nombre bien
                print (f"El nombre es {nombre}")
    
                # creamos el objeto BeautifulSoup para poder acceder al contenido solicitado
                sopa = BeautifulSoup(respuesta.content, 'html.parser')
    
                #buscamos tablas
                tabla_bio = sopa.find("table")
    
                # separar la tabla en una lista con distintos datos separados
                celdas = tabla_bio.find_all('td')
    
                # Extraer el texto de cada celda y dividirlo por espacios
                lista_resultados_pre = [celda.get_text(strip=True, separator=' ') for celda in celdas]
                print(lista_resultados_pre)
    
    
                #en wikipedia puede escribir cualquiera por lo que los datos no están siempre ordenados del mismo modo, ni contiene lo mismo, por lo que hay que buscar cada dato teniendo en cuenta el contenido de cada celda
                meses = ["enero", "febrero", "marzo", "abril", "mayo", "junio", "julio", "agosto", "septiembre", "octubre", "noviembre", "diciembre"]
                
                for elemento in lista_resultados_pre:
                    #activo desde:
                    patron = re.compile(r"^desde\s\d{4}$") #con un patron regex buscamos los resultados que sean iguales a "desde" y un año, estos resultados los guardamos como el año desde que esán activos
                    if patron.search(elemento):
                        activo = elemento.split()[-1]
                        print(f"Activo desde: {activo}")
                
                    # año nacimiento
                    for mes in meses: #las fechas de nacimiento son las únicas que se muestran al completo, por lo que, si el tiene algún mes, lo guardamos como fecha de nacimiento
                        if mes in elemento:
                            if "Este artículo" not in elemento:
                                fecha_nacimiento = elemento.split("(")[0]
                                print(f"La fecha de nacimiento es: {fecha_nacimiento}")
    
                            #pais de nacimiento
                            pais_nacimiento = elemento.replace(")","").split()[-1] #la fecha de nacimiento viene unida al lugar de nacimiento por lo que, al separarlo, cogemos el último elemento y lo guardamos como pais de nacimiento
                            if pais_nacimiento == "Unidos":  #para los paises con dos palabras hacemos ifs especificos
                                pais_nacimiento = "Estados Unidos"
                            if pais_nacimiento == "Unido":
                                pais_nacimiento = "Reino Unido"
                            if pais_nacimiento == "Bajos":
                                pais_nacimiento = "Paises Bajos"
                            if pais_nacimiento == "Sur":
                                pais_nacimiento = "Corea del Sur"
                            if pais_nacimiento == "Dominicana":
                                pais_nacimiento = "Republica Dominicana"
                            if pais_nacimiento == "Rico":
                                pais_nacimiento = "Puerto Rico"
                            if ")" in pais_nacimiento:       #hemos tenido que solucionar unos problemas concretos que hemos encontrado:
                                pais_nacimiento.replace(")","")
                            if pais_nacimiento == patron:
                                pais_nacimiento = "sin dato"
                            if pais_nacimiento == re.compile(r"^desde\s\d{4}$\."):
                                pais_nacimiento = "sin dato"
    
                            print(f"El país de nacimiento es: {pais_nacimiento}")
    
                #para los premios hemos tenido que buscar los elementos que coincidan con los premios de interpretacion y meterlos en una lista ya que la mayoría de veces son varios
                premios = []  
                for elemento in lista_resultados_pre:           
                    premios_lista = ["Oscar", "Globo de Oro", "BAFTA", "León de Oro","Palma de Oro","Oso de Oro","SAG","Critics' Choice","Goya","Oso de Plata","Emmy", "Tony","Concha de Plata","Premio ", "Mejor", "Award"]
                    for premio in premios_lista:
                        if premio in elemento:
                            premios.append(elemento)
    
                for elemento in premios: #quitamos uno de los elementos que coincide con el nombre de un premio pero es un sindicato
                    if "Sindicato" in elemento:
                        premios.remove(elemento)
    
                print(f"Los premios son: {premios}")
                actor_datos = (nombre, fecha_nacimiento, pais_nacimiento, activo, premios)
                actores_datos.append(actor_datos)
                print("-----------------")
    
            else:
                print("sin wikipedia") #printeamos para los que no tienen página de wikipedia
        except:
            print("--------------")
          
    return actores_datos

0


La respuesta de la petición es: 404
sin wikipedia
[]
1
La respuesta de la petición es: 404
sin wikipedia
[]
2
La respuesta de la petición es: 404
sin wikipedia
[]
3
La respuesta de la petición es: 404
sin wikipedia
[]
4
La respuesta de la petición es: 404
sin wikipedia
[]
5
La respuesta de la petición es: 200
El nombre es Joanna Cassidy
['', '2 de agosto de 1945 (78 años) Haddonfield ( Estados Unidos )', 'Estadounidense', 'Inglés', 'Universidad de Siracusa Haddonfield Memorial High School', 'Actriz , modelo , actriz de televisión, actriz de cine y actriz de voz', 'desde 1968', 'SAG-AFTRA', '[ editar datos en Wikidata ]']
La fecha de nacimiento es: 2 de agosto de 1945 
El país de nacimiento es: Estados Unidos
Activo desde: 1968
Los premios son: []
-----------------
[('Joanna Cassidy', '2 de agosto de 1945 ', 'Estados Unidos', '1968', [])]
6
La respuesta de la petición es: 200
El nombre es Bill Moseley
['Bill Moseley en enero de 2006', 'William Moseley', '11 de noviembre de 1951 (72\xa0a

In [34]:
df_actores_datos = pd.DataFrame(actores_datos)

In [36]:
df_actores_datos.tail()

0                          1               2     3   4
78     Hank Azaria       25 de abril de 1964   Estados Unidos  1986  []
79  Keir Gilchrist  28 de septiembre de 1992      Reino Unido  2003  []
80    Emma Roberts     28 de febrero de 1991   Estados Unidos  2003  []
81     Viola Davis      11 de agosto de 1965   Estados Unidos  2003  []
82   Lauren Graham       16 de marzo de 1967   Estados Unidos  2003  []